In [1]:
import pbj

In [4]:
simulation = pbj.electrostatics.Simulation(formulation="direct")
ubq = pbj.electrostatics.Solute("1ubq.pqr", mesh_density=1)
simulation.add_solute(ubq)



 <<INFO>> Starting NanoShaper 0.7.8
 <<INFO>> Loading atoms....
 <<INFO>> Read 1231 atoms
 <<INFO>> Geometric baricenter ->  30.5399 29.4191 17.9425
 <<INFO>> Grid is 35
 <<INFO>> MAX 51.7899 50.6691 39.1925
 <<INFO>> MIN 9.2899 8.1691 -3.3075
 <<INFO>> Perfil 90 %
 <<INFO>> Rmaxdim 39.9394
 <<INFO>> Allocating memory...ok!
 <<INFO>> Initialization completed
 <<INFO>> Adjusting self intersection grid 
 <<INFO>> Self intersection grid is (before) 28
 <<INFO>> Self intersection grid is 16
 <<INFO>> Allocating self intersection grid....ok!
 <<INFO>> Computing alpha shape complex....ok!
 <<INFO>> Checking 172 probes for self intersections...ok!
 <<INFO>> Surface build-up time.. 0 [s]
 <<INFO>> Probe Radius value 1.4
 <<INFO>> Number of ses cells -> 3167
 <<INFO>> Number of del_point cells -> 504
 <<INFO>> Number of regular del_edge cells -> 1558
 <<INFO>> Number of singular del_edge cells -> 1
 <<INFO>> Number of regular del_facet cells -> 1016
 <<INFO>> Number of singular del_facet cell

In [5]:
simulation.calculate_solvation_energy()
print(simulation.solutes[0].results["solvation_energy"])

/home/chris/miniconda3/envs/pbj/lib/python3.9/site-packages/pyopencl/__init__.py:270: CompilerWarning: Non-empty compiler output encountered. Set the environment variable PYOPENCL_COMPILER_OUTPUT=1 to see more.
  warn("Non-empty compiler output encountered. Set the "


-325.7201360515149


In [4]:
import matplotlib as mpl
from matplotlib import pyplot as plt
import numpy as np
import plotly
import plotly.figure_factory as ff
import plotly.graph_objs as go
    
    
def extract_gf(obj, unit_conv):
    
    grid = obj.space.grid
    vertices = grid.vertices
    elements = grid.elements

    local_coordinates = np.array([[1.0 / 3], [1.0 / 3]])
    values = np.zeros(grid.entity_count(0), dtype="float64")
    for element in grid.entity_iterator(0):
        index = element.index
        local_values = np.real(
            np.real(obj.evaluate(index, local_coordinates))
        )
        values[index] = local_values.flatten()
        
    values *= unit_conv
    return vertices, elements, values
        
        
def plot_surface(self, cmap_name="bwr_r", val_max=None, val_min=None):
    
    cmap = plt.get_cmap(cmap_name)
    
    values_sort_index = np.argsort(values)
    
    if val_max==None:
        val_max = np.max(values)
    if val_min==None:
        val_min = np.min(values)
        
    val_mid = (val_max+val_min)/2

    norm = mpl.colors.Normalize(vmin=val_min, vmax=val_max, clip=True)
    colorfun = lambda x: np.rint(np.array(cmap(norm(x))) * 255)
    color_codes = ["rgb({0}, {1}, {2})".format(*colorfun(x)) for x in values]
    color_codes = np.array(color_codes)
    color_codes_sort = color_codes[values_sort_index]

    
    fig = ff.create_trisurf(
        x=vertices[0, :],
        y=vertices[1, :],
        z=vertices[2, :],
        simplices=elements.T,
        color_func=color_codes,
        plot_edges=False,
        showbackground=False,
        show_colorbar=True
    )
    colorbar_codes = [[],[],[]]
    colorbar_codes[0] = "rgb({0}, {1}, {2})".format(*colorfun(val_min))
    colorbar_codes[1] = "rgb({0}, {1}, {2})".format(*colorfun(val_mid))
    colorbar_codes[2] = "rgb({0}, {1}, {2})".format(*colorfun(val_max))
    colorbar_trace=go.Scatter(x=[None],
             y=[None],
             mode='markers',
             opacity=0,
             marker=dict(
                 colorscale=colorbar_codes, 
                 showscale=True,
                 cmin=val_min,
                 cmax=val_max,
                 colorbar=dict(thickness=10, tickvals=[val_min, val_mid, 0, val_max], ticktext=["%1.4f"%val_min, "%1.4f"%val_mid, "%1.4f"%0., "%1.4f"%val_max]), 
             ),
             hoverinfo='none'
            )
    
    fig["layout"]["scene"].update(go.layout.Scene(aspectmode="data"))
    fig["data"][0].update(opacity=1.)
    
    fig.update_layout({
    "plot_bgcolor": "rgba(0, 0, 0, 0)",
    "paper_bgcolor": "rgba(0, 0, 0, 0)",
    "xaxis":dict(showticklabels=False),
    "yaxis":dict(showticklabels=False),
    })
    
    #layout = dict(xaxis=dict(visible=False), yaxis=dict(visible=False))#, paper_bgcolor='rgba(0,0,0,0)', plot_bgcolor='rgba(0,0,0,0)')
    
    fig.add_trace(colorbar_trace)

    #fig = go.Figure([dummy_trace], layout)
    plotly.offline.iplot(fig)
    

In [5]:
unit_conv_pbj = 180.9513*1000 # PBJ potential to mV
vertices, elements, values = extract_gf(simulation.solutes[0].results["phi"], unit_conv_pbj)

In [7]:
plot_surface(vertices, elements, values, val_min=-128, val_max=128)

In [3]:
from vtk_poly_to_msms import vtk_to_msms

In [4]:
tabi_data = vtk_to_msms("1ubq/tabi_results/surface_potential.vtk")

In [10]:
qe = 1.60217663e-19
Na = 6.02214076e23
unit_factor = 1e6/(Na*qe*4.184) # TABI kJ/mol/qe to mV
plot_surface(tabi_data["vertices"].T, tabi_data["faces"].T, tabi_data["PotentialFace"]*unit_factor, val_min=-110, val_max=110)

In [ ]:
diff_pbj_tabi = values - tabi_data["PotentialFace"]*unit_factor

In [ ]:
plot_surface(tabi_data["vertices"].T, tabi_data["faces"].T, diff_pbj_tabi, val_min=-10, val_max=10)

In [12]:
import pickle
import os
import MDAnalysis as mda
from gridData import Grid


In [13]:
work_folder = "1ubq/"
data_full = pickle.load(open(work_folder+"results_1ubq_base.pickle","rb"))
dx_file = work_folder + data_full[0]["dx_folder"].split("/")[1] + "/" + data_full[0]["pot_solv-state"] + ".dx"

In [14]:
print(data_full[0])

{'dime_tag': '129', 'dx_folder': '1ubq/1ubq_base_dx_files', 'pot_solv-state': 'potential_solv_129', 'pot_ref-state': 'potential_vac_129', 'pqr': '1ubq.pqr', 'mol': '1', 'bcfl': 'mdh', 'pdie': '4.0000', 'sdie': '80.0000', 'srfm': 'mol', 'chgm': 'spl2', 'sdens': '10.00', 'srad': '1.40', 'swin': '0.30', 'temp': '298.15', 'calcenergy': 'total', 'calcforce': 'no', 'grid_dime': ' 129 x 129 x 129', 'grid_spacing': ' 0.391 x 0.391 x 0.391', 'grid_length': ' 50.000 x 50.000 x 50.000', 'solvation_energy': '-1.159111213765E+03'}


In [15]:
grid = Grid(dx_file)

In [16]:
x = grid.midpoints[0]
y = grid.midpoints[1]
z = grid.midpoints[2]

In [20]:
from scipy.interpolate import RegularGridInterpolator


In [21]:
import scipy
print(scipy.__version__)

1.5.3


In [22]:
fn = RegularGridInterpolator((x,y,z), grid.grid, method="linear")

In [23]:
apbs_vals = fn(simulation.solutes[0].mesh.centroids)*25.8 #mV

In [25]:
plot_surface(tabi_data["vertices"].T, tabi_data["faces"].T, apbs_vals, val_min=-128, val_max=128)

In [6]:
center = np.average(tabi_data["vertices"], axis=0)
dist = np.linalg.norm(tabi_data["vertices"] - center, axis=1)
dist_max = np.max(dist)
dist_min = np.min(dist)

In [7]:
box = simulation.solutes[0].mesh.bounding_box

In [8]:
help(simulation.solutes[0].mesh)

Help on Grid in module bempp.api.grid.grid object:

class Grid(builtins.object)
 |  Grid(vertices, elements, domain_indices=None, grid_id=None, scatter=True)
 |  
 |  The Grid class.
 |  
 |  Methods defined here:
 |  
 |  __init__(self, vertices, elements, domain_indices=None, grid_id=None, scatter=True)
 |      Create a grid from a vertices and an elements array.
 |  
 |  data(self, precision='double')
 |      Return Numba container with all relevant grid data.
 |  
 |  entity_count(self, codim)
 |      Return the number of entities of given codimension.
 |  
 |  entity_iterator(self, codim)
 |      Return an iterator for a given codim.
 |  
 |  get_element(self, index)
 |      Return element with a given index.
 |  
 |  map_to_point_cloud(self, order=None, local_points=None, precision='double')
 |      Return a point cloud representation of the grid on quadratur points.
 |      
 |      Return a representation of the grid as a point cloud using points on
 |      each element either 

In [9]:
print(dist_max)
print(dist_min)

26.29925075268289
6.386387435018112


In [10]:
# mask out points in solute
import trimesh


In [17]:
XX,YY,ZZ = np.meshgrid(x,y,z)
XX = XX.flatten()
YY = YY.flatten()
ZZ = ZZ.flatten()
d = np.sqrt((XX-center[0])**2+(YY-center[1])**2+(ZZ-center[2])**2)

In [18]:
xmin = box[0,0]; xmax = box[0,1]
ymin = box[1,0]; ymax = box[1,1]
zmin = box[2,0]; zmax = box[2,1]

inside_x = np.logical_and(XX>xmin-2, XX<xmax+2)
inside_y = np.logical_and(YY>ymin-2, YY<ymax+2)
inside_z = np.logical_and(ZZ>zmin-2, ZZ<zmax+2)

inside_box = np.logical_and(inside_x, inside_y)
inside_box = np.logical_and(inside_box, inside_z)

box_index = np.nonzero(inside_box)

In [19]:
len(box_index[0])

1054944

In [20]:
inside_sphere = np.logical_and(d<dist_max+2, d>dist_min)
close_by = np.logical_and(inside_box,inside_sphere)
close_by_index = np.nonzero(close_by)
XX_close = XX[close_by_index]
YY_close = YY[close_by_index]
ZZ_close = ZZ[close_by_index]

In [21]:
print(len(XX_close))
print(len(XX))

991697
2146689


In [40]:
inside_protein_layer = np.zeros(len(XX_close), dtype=int)
for i in range(len(XX_close)):
    dx = XX_close[i] - simulation.solutes[0].x_q[:,0]
    dy = YY_close[i] - simulation.solutes[0].x_q[:,1]
    dz = ZZ_close[i] - simulation.solutes[0].x_q[:,2]
    
    dist_to_atoms = np.sqrt(dx*dx+dy*dy+dz*dz)
    
    is_inside = np.nonzero(dist_to_atoms < simulation.solutes[0].r_q)
    is_inside_layer = np.nonzero(dist_to_atoms < simulation.solutes[0].r_q + 2)

    if len(is_inside[0])==0 and len(is_inside_layer[0])>0:
        inside_protein_layer[i] = 1
        
print(np.sum(inside_protein_layer))

174920


In [41]:
close_atoms = np.nonzero(inside_protein_layer)[0]
XX_close_2 = XX_close[close_atoms]
YY_close_2 = YY_close[close_atoms]
ZZ_close_2 = ZZ_close[close_atoms]

In [42]:
points_solvent = np.ones(np.shape(XX_close_2)[0], dtype=bool)

In [43]:
mesh_tri = trimesh.Trimesh(vertices = tabi_data["vertices"], faces = tabi_data["faces"])

In [44]:
eval_points = np.zeros((len(XX_close_2),3))
eval_points[:,0] = XX_close_2
eval_points[:,1] = YY_close_2
eval_points[:,2] = ZZ_close_2

In [ ]:
points_solute = mesh_tri.contains(eval_points)

In [ ]:
points_solvent = np.logical_and(points_solvent, np.logical_not(points_solute))

In [ ]:
1873185435/2146689

In [ ]:
len(tabi_data["vertices"])

In [6]:
fagbi_output = np.loadtxt("1ubq/fagbi_results/1ubq_pot.txt")
fagbi_values = fagbi_output[:len(fagbi_output)//2]

In [7]:
unit_conv_pbj = 180.9513*1000
fagbi_pot = fagbi_values*unit_conv_pbj

In [9]:
plot_surface(tabi_data["vertices"].T, tabi_data["faces"].T, fagbi_pot, val_min=-110, val_max=110)

In [ ]:
import dash
import dash_bio as dashbio
from dash import html
from dash_bio.utils import PdbParser, create_mol3d_style
from dash.dependencies import Input, Output

app = dash.Dash(__name__)

parser = PdbParser('1ubq/1ubq.pdb')

data = parser.mol3d_data()
styles = create_mol3d_style(
    data['atoms'], visualization_type='cartoon', color_element='residue'
)

app.layout = html.Div([
    dashbio.Molecule3dViewer(
        id='dashbio-default-molecule3d',
        modelData=data,
        styles=styles
    ),
    "Selection data",
    html.Hr(),
    html.Div(id='default-molecule3d-output')
])

@app.callback(
    Output('default-molecule3d-output', 'children'),
    Input('dashbio-default-molecule3d', 'selectedAtomIds')
)
def show_selected_atoms(atom_ids):
    if atom_ids is None or len(atom_ids) == 0:
        return 'No atom has been selected. Click somewhere on the molecular \
        structure to select an atom.'
    return [html.Div([
        html.Div('Element: {}'.format(data['atoms'][atm]['elem'])),
        html.Div('Chain: {}'.format(data['atoms'][atm]['chain'])),
        html.Div('Residue name: {}'.format(data['atoms'][atm]['residue_name'])),
        html.Br()
    ]) for atm in atom_ids]

app.run_server(debug=True)